In [ ]:
%matplotlib inline

import matplotlib

import matplotlib.pyplot as plt
import pandas as pd
from math import sqrt
import sys

In [ ]:
def print_first_lines(path, number_of_lines):
    with open(path, 'r') as f:
        for i in range(number_of_lines):
            print f.readline()
    f.close()

 <h3>5-2 Frequent Itemset Mining on Bakery Receipts</h3>

In [ ]:
print_first_lines('75000-out1.csv', 4)

In [ ]:
with open('75000-out1.csv', 'r') as f:
    dataset = f.read().splitlines()
dataset = [[int(cur) for cur in cur_line.split(', ')[1:]] for cur_line in dataset]
        


In [ ]:
dataset[:3]

In [ ]:
with open('goods_description.csv', 'r') as f:
    for i in range(4):
        print f.readline()

In [ ]:
goods_mapping = pd.read_csv('goods_description.csv', index_col='ID')

In [ ]:
print goods_mapping.head(3)
print goods_mapping.tail(3)
print goods_mapping.shape

In [ ]:
def replace_id(dataset, mapping_columns = 'ARTICLE', mapping_dic = goods_mapping):
    dataset_mapped = [[goods_mapping.iloc[current_id][mapping_columns]\
                        for current_id in current_itemset]\
                        for current_itemset in dataset]
    if type(mapping_columns)==str:
        return dataset_mapped 
    return[['_'.join(list(item_representation)) for item_representation in current_itemset]\
            for current_itemset in\
           dataset_mapped]

In [ ]:
dataset_fine_granular = replace_id(dataset, mapping_columns=['ARTICLE', 'CATEGORY'])

In [ ]:
dataset_fine_granular[:5]

In [ ]:
from fim import apriori
from fim import fpgrowth

In [ ]:
help(apriori)

In [ ]:
sorted(apriori(dataset_fine_granular, report='as', supp = 5), key = lambda (a,b,c):-b)

In [ ]:
sorted(apriori(dataset_fine_granular, report='as', supp = 5, zmin=2), key = lambda (a,b,c):-b)

In [ ]:
sorted(fpgrowth(dataset_fine_granular, report='as', supp = 5, zmin=2), key = lambda (a,b,c):-b)

Expected support for pairs:
$$P(X,Y) = P(X) \times P(Y)$$ 
$$E[support(X,Y)] = |T| \times P(X,Y)$$
$$75000 \times \frac{1}{50^{2}} = 30$$
$$30/75000 = 0.0004 = 0.04\%$$



In [ ]:
from fim import arules

In [ ]:
arules(dataset_fine_granular, supp = 5, conf=50)

In [ ]:
arules(dataset_fine_granular, supp = 1, conf=50)

In [ ]:
arules(dataset_fine_granular, supp = 5, conf=50, report='Cl')

In [ ]:
arules(dataset_fine_granular, supp = 1, conf=50, report='Cl')

In [ ]:
dataset_categories = replace_id(dataset, mapping_columns=['CATEGORY'])

In [ ]:
dataset_categories[:3]

In [ ]:
arules(dataset_categories, supp = 1, conf=90, report='Cl')

In [ ]:
0.91/1.66

In [ ]:
apriori(dataset_categories, supp=54)

<h3> 5.3 K-means</h3>


In [ ]:
print_first_lines('blobs.csv', 4)

In [ ]:
blobs_dataset = pd.read_csv('blobs.csv', header=None)

In [ ]:
def visualize(dataset, centroids = None, labels = None, figure_number = 0):
    colors = ['g', 'b', 'c', 'm', 'k']
    #necessary due to pandas bug
    if labels is not None:
        c = [colors[i] for i in labels.map(int).tolist()]
    else:
        c = colors[0]
    plt.figure(figure_number)
    ax = plt.scatter(dataset[0],\
                dataset[1],\
                color = c)
    if centroids:
        for current_c in centroids:
            plt.scatter(current_c[0], current_c[1], color = 'r', marker='+', s=80)
    

In [ ]:
visualize(blobs_dataset, None)

In [ ]:
def assign_label(point, centroids):
    best_error = sys.float_info.max
    best_label = -1
    for i in range(len(centroids)):
        dif = point - centroids[i]
        error = sum([cur_diff**2 for cur_diff in dif])
        if error < best_error:
            best_error = error
            best_label = i
    return [best_label, best_error]
    
    
    

In [ ]:
def kmeans(data,k, max_iteration = 20):
    centroids = data.sample(k).values.tolist()
    current_sse = sys.float_info.max
    tolerance = 1e-5
    iteration = 0
    while True:
        previous_sse = current_sse
        label_error = data.apply(lambda row:assign_label(row, centroids), axis=1)
        label_error.columns = ['label', 'error']
        current_sse = label_error['error'].sum()
        if previous_sse-current_sse < tolerance or iteration == max_iteration:
            break
        print 'iteration %s, sse=%s'%(iteration, current_sse)
        visualize(data, centroids, label_error['label'], figure_number=iteration)
        centroids = []
        for i in range(k):
            cluster_objects = data[label_error['label'] == i]
            cluster_size = cluster_objects.shape[0]
            centroid = cluster_objects.sum(axis = 0)/cluster_size
            centroids.append(centroid)
        iteration += 1
            
        

In [ ]:
kmeans(blobs_dataset, 4)

In [ ]:
mouse_dataset = pd.read_csv('mouse.csv', header=None)

In [ ]:
visualize(mouse_dataset, None)

In [ ]:
kmeans(mouse_dataset, 3)